In [1]:
import re
import pandas as pd

from Bio import SeqIO
from Bio.SeqRecord import SeqRecord
from Bio.Blast.Applications import NcbiblastpCommandline

import matplotlib.pyplot as plt

from collections import Counter

from pepmatch import Matcher


from anytree import Node, RenderTree

def add_nodes(nodes, parent, child):
    if parent not in nodes:
        nodes[parent] = Node(parent)  
    if child not in nodes:
        nodes[child] = Node(child)
    nodes[child].parent = nodes[parent]

In [2]:
proteins = list(SeqIO.parse('9606_all.fasta', 'fasta'))
gp_ids = [str(x.id.split('|')[1]) for x in list(SeqIO.parse('9606_gp.fasta', 'fasta'))]

In [95]:
data = []
for protein in proteins:
    uniprot_id = protein.id.split('|')[1]
    try:
        gene = re.search('GN=(.*?) ', protein.description).group(1)
    except AttributeError:
        try:
            gene = re.search('GN=(.*?)$', protein.description).group(1)
        except AttributeError:
            gene = ''
    
    gp = 1 if uniprot_id in gp_ids else 0
    
    try:
        pe_level = int(re.search('PE=(.*?) ', protein.description).group(1))
    except AttributeError:
        pe_level = 0
    
    data.append([protein.id.split('|')[0], gene, uniprot_id, gp, pe_level, str(protein.seq)])
    
df = pd.DataFrame(data, columns=['db', 'gene', 'id', 'gp', 'pe_level', 'seq'])

In [96]:
# use hugo mappings to map old symbols to new symbols
hugo = pd.read_csv('hugo_symbol_map.csv')
# remove unmatched input so as to not insert NaNs
hugo = hugo[hugo['Match type'] == 'Approved symbol']
hugo_map = dict(zip(hugo['Input'], hugo['Approved symbol']))
df['gene'] = df['gene'].map(hugo_map).fillna(df['gene'])

In [97]:
nodes = {}
for parent, child in zip(df['gene'],df['id']):
    add_nodes(nodes, parent, child)

with open('protein_tree.txt', 'w') as f:
    roots = list(df[~df['gene'].isin(df['id'])]['gene'].unique())
    for root in roots:
        for pre, _, node in RenderTree(nodes[root]):
            if node.name in gp_ids:
                f.write("%s%s*" % (pre, node.name))
                f.write('\n')
            else:
                f.write("%s%s" % (pre, node.name))
                f.write('\n')

In [98]:
df.to_csv('human_proteome.csv', index=False)

In [7]:
gp_mapping = {}
for i, group in df.groupby('gene'):
    for id in list(group['id']):
        try:
            gp_mapping[id] = str(group[group['gp'] == 1]['id'].iloc[0])
        except IndexError:
            pass

In [8]:
import pickle
with open('canonical_protein_mapping.pickle', 'wb') as f:
    pickle.dump(gp_mapping, f)

In [9]:
with open('all_genes.txt', 'w') as f:
    for gene in df['gene'].unique():
        f.write(str(gene) + '\n')

In [2]:
def has_numbers(seq):
    return any(s.isdigit() for s in seq)

has_numbers('T314, V315, G316, E317, N320, K350, S367, P369, R370, L371, K372, P373, E375, P401, P402, E403, V491, S493, G494')

True

In [182]:
epitopes

Epitope ID  Start    End Source Accession  \
0            151086    NaN    NaN         P49765.2   
1            768060  482.0  493.0           P11597   
2            768058  477.0  487.0           P11597   
3            768059  477.0  490.0           P11597   
4            557400  193.0  205.0         O43570.1   
...             ...    ...    ...              ...   
1454674      604804  154.0  163.0       AAH05807.1   
1454675      770505  254.0  264.0       AAH33897.2   
1454676      770506  328.0  336.0       AAC50951.1   
1454677      604805    4.0   12.0       AAH03667.1   
1454678      434831  195.0  205.0       AAH09564.1   

                                  Source Name  \
0        Vascular endothelial growth factor B   
1          Cholesteryl ester transfer protein   
2          Cholesteryl ester transfer protein   
3          Cholesteryl ester transfer protein   
4                       Carbonic anhydrase 12   
...                                       ...   
1454674                           SCD protein   
1454675    Chromosome 3 open reading frame 19   
1454676       lanosterol 14-alpha demethylase   
1454677            Ribosomal protein S27-like   
1454678                            annexin A2   

                                                   Peptide  Organism ID  \
0        A: S37, W38, I39, Y42, T46, C47, Q48, P83, C12...       9606.0   
1                                             EHLLVDFLQSLS       9606.0   
2                                              DFGFPEHLLVD       9606.0   
3                                           DFGFPEHLLVDFLQ       9606.0   
4                                            VKYKGQEAFVPGF       9606.0   
...                                                    ...          ...   
1454674                                         ARDHRAHHKF       9606.0   
1454675                                        ARDKELRNKQM       9606.0   
1454676                                          ARDKTLQKK       9606.0   
1454677                                          ARDLLHPSL       9606.0   
1454678                                        ARDLYDAGVKR       9606.0   

                Organism Name  
0        Homo sapiens (human)  
1        Homo sapiens (human)  
2        Homo sapiens (human)  
3        Homo sapiens (human)  
4        Homo sapiens (human)  
...                       ...  
1454674  Homo sapiens (human)  
1454675  Homo sapiens (human)  
1454676  Homo sapiens (human)  
1454677  Homo sapiens (human)  
1454678  Homo sapiens (human)  

[1454150 rows x 8 columns]

In [3]:
sources = pd.read_csv('/home/dan/projects/protein_tree/snapshot_2022-12-20/vertebrate/9606-Homo-sapiens-human/sources.tsv', sep='\t')
epitopes = pd.read_csv('/home/dan/projects/protein_tree/snapshot_2022-12-20/vertebrate/9606-Homo-sapiens-human/epitopes.tsv', sep='\t')

sources.dropna(subset=['Source Sequence'], inplace=True)
epitopes.dropna(subset=['Peptide'], inplace=True)

# remove epitopes less than 5 residues
epitopes = epitopes[epitopes['Peptide'].str.len() >= 5]

In [4]:
epitope_map = {}
for i, row in epitopes.iterrows():
    if has_numbers(row['Peptide']):
        continue
    if row['Source Accession'] in epitope_map.keys():
        epitope_map[row['Source Accession']].append(row['Peptide'])
    else:
        epitope_map[row['Source Accession']] = [row['Peptide']]

In [5]:
epitope_map

{'P11597': ['EHLLVDFLQSLS',
  'DFGFPEHLLVD',
  'DFGFPEHLLVDFLQ',
  'RDGFLLLQMDFGFPEHLLVDFLQSLS',
  'DFGFPEHLL',
  'FPEHLLVDF',
  'FPEHLLVDFL',
  'TAVGIPEVM',
  'VVFKGTLKY',
  'FQITPKTV',
  'SEDLPLPTF',
  'FPRPDQQHSV',
  'GDPVI',
  'ITASY',
  'NPEIIT',
  'ASYLESHHKGHFIYKNVSEDLPLPTFSPTLLGDS',
  'SQAQVTVHCLKMPKIS',
  'AYTFEED',
  'TVSNLTESSSESVQSFLQ',
  'FPRPDQQHSV',
  'VVFKGTLKY',
  'ISLTG',
  'FGFPEHLLVDFLQSLS',
  'YPDITGEKAM',
  'NFISFTLKL',
  'YSKKKLFL',
  'VVFKGTLKY',
  'FEEDIVTTV',
  'IVTTVQASY',
  'ETAKVIQTA',
  'KEINVISNI',
  'EIFQEVVGGF',
  'FLQSMITAV',
  'FVQTRAASILSDG',
  'FVQTRAASI',
  'REPGWIKQLF',
  'SEDLPLPTF'],
 'O43570.1': ['VKYKGQEAFVPGF', 'QVCTAAGLSLGII', 'DERLVYTSF'],
 'NP_004480.1': ['SQNPRFYHK',
  'SQNPRFYHK',
  'MEHANQQTGF',
  'RPKLSNAM',
  'MEHANQQTGF',
  'HYVGSAAAF',
  'SQNPRFYHK',
  'HFQPTQTGF',
  'GHFQPTQTGF',
  'EHANQQTGF',
  'SQNPRFYHK',
  'MEHANQQTGF',
  'SQNPRFYHK',
  'SQNPRFYHK',
  'SQPGPRLPFI',
  'SQNPRFYHK',
  'KQMEHANQQTGF',
  'MEHANQQTGF',
  'HYVGSAAAF'

In [6]:
sources

Source ID Source Accession Database  \
1          282897         P07333.2  GenPept   
2          282804   XP_006710671.1  GenPept   
3          282805      NP_997320.2  GenPept   
4          282806   XP_005246254.1  GenPept   
6          282807       BAB13945.1  GenPept   
...           ...              ...      ...   
125459     547724   NP_001139131.1  GenPept   
125460     547726         47169548  GenPept   
125461     547727        937628440  GenPept   
125462     547728       EAW77955.1  GenPept   
125463     547730       QBK47418.1  GenPept   

                                            Source Name Aliases  \
1       Macrophage colony-stimulating factor 1 receptor     NaN   
2           arylacetamide deacetylase-like 4 isoform X1     NaN   
3                       dynein heavy chain 10, axonemal     NaN   
4                              protein GREB1 isoform X7     NaN   
6                               unnamed protein product     NaN   
...                                                 ...     ...   
125459             cTAGE family member 9 [Homo sapiens]     NaN   
125460         TPA: ovostatin-2, partial [Homo sapiens]     NaN   
125461                            OR2A25 [Homo sapiens]     NaN   
125462                          hCG32758 [Homo sapiens]     NaN   
125463        immunoglobulin heavy chain [Homo sapiens]     NaN   

                                                 Synonyms  \
1       CSF-1 receptor, Proto-oncogene c-Fms, CSF-1-R,...   
2                                                     NaN   
3       dynein, axonemal, heavy polypeptide 10, ciliar...   
4                                                     NaN   
6                                                     NaN   
...                                                   ...   
125459  cutaneous T-cell lymphoma-associated antigen 9...   
125460                                                NaN   
125461                                                NaN   
125462                                                NaN   
125463                                                NaN   

                                          Source Sequence  Organism ID  \
1       MGPGVLLLLLVATAWHGQGIPVIEPSVPELVVKPGATVTLRCVGNG...       9606.0   
2       MPKFIRFLHDSVRIKKDPELVVTDLRFGTIPVRLFQPKAASSRPRR...       9606.0   
3       MVPEEVEVEIDEIPVLSEEGEEEEETYSQKVESVDKVRAKRVSLRT...       9606.0   
4       MWQKIEDVEWRPQTYLELEGLPCILIFSGMDPHGESLPRSLRYCDL...       9606.0   
6       MGTDEQTDFGLGDAHQSDGLNLEREIVSQTTATQEKSQEELPTTNN...       9606.0   
...                                                   ...          ...   
125459  MEEPGATPQPYLGLVLEELGRVVAALPESMRPDENPYGFPSELVVC...       9606.0   
125460  QYVLLIPSVLQEGSLDKACAQLFNLTESVVLTVSLNYGEVQTKIFE...       9606.0   
125461  MGGNQTSITEFLLLGFPIGPRIQMLLFGLFSLFYIFILLGNGTILG...       9606.0   
125462  MPSHLNQHQIIHTKEKSYKCEECGKSFKRSSNCTTHKRIHTGEKPY...       9606.0   
125463  MELGLCWVFLVAILKGVQCEVQLVESGGGLVQPGGSLRLSCAASGF...       9606.0   

               Organism Name    Status  
1       Homo sapiens (human)    Active  
2       Homo sapiens (human)    Active  
3       Homo sapiens (human)    Active  
4       Homo sapiens (human)    Active  
6       Homo sapiens (human)    Active  
...                      ...       ...  
125459  Homo sapiens (human)  Inactive  
125460  Homo sapiens (human)  Inactive  
125461  Homo sapiens (human)  Inactive  
125462  Homo sapiens (human)  Inactive  
125463  Homo sapiens (human)  Inactive  

[124993 rows x 10 columns]

In [7]:
epitopes

Epitope ID  Start    End Source Accession  \
0            151086    NaN    NaN         P49765.2   
1            768060  482.0  493.0           P11597   
2            768058  477.0  487.0           P11597   
3            768059  477.0  490.0           P11597   
4            557400  193.0  205.0         O43570.1   
...             ...    ...    ...              ...   
1454674      604804  154.0  163.0       AAH05807.1   
1454675      770505  254.0  264.0       AAH33897.2   
1454676      770506  328.0  336.0       AAC50951.1   
1454677      604805    4.0   12.0       AAH03667.1   
1454678      434831  195.0  205.0       AAH09564.1   

                                  Source Name  \
0        Vascular endothelial growth factor B   
1          Cholesteryl ester transfer protein   
2          Cholesteryl ester transfer protein   
3          Cholesteryl ester transfer protein   
4                       Carbonic anhydrase 12   
...                                       ...   
1454674                           SCD protein   
1454675    Chromosome 3 open reading frame 19   
1454676       lanosterol 14-alpha demethylase   
1454677            Ribosomal protein S27-like   
1454678                            annexin A2   

                                                   Peptide  Organism ID  \
0        A: S37, W38, I39, Y42, T46, C47, Q48, P83, C12...       9606.0   
1                                             EHLLVDFLQSLS       9606.0   
2                                              DFGFPEHLLVD       9606.0   
3                                           DFGFPEHLLVDFLQ       9606.0   
4                                            VKYKGQEAFVPGF       9606.0   
...                                                    ...          ...   
1454674                                         ARDHRAHHKF       9606.0   
1454675                                        ARDKELRNKQM       9606.0   
1454676                                          ARDKTLQKK       9606.0   
1454677                                          ARDLLHPSL       9606.0   
1454678                                        ARDLYDAGVKR       9606.0   

                Organism Name  
0        Homo sapiens (human)  
1        Homo sapiens (human)  
2        Homo sapiens (human)  
3        Homo sapiens (human)  
4        Homo sapiens (human)  
...                       ...  
1454674  Homo sapiens (human)  
1454675  Homo sapiens (human)  
1454676  Homo sapiens (human)  
1454677  Homo sapiens (human)  
1454678  Homo sapiens (human)  

[1454150 rows x 8 columns]

In [8]:
# read in human proteome data
hp = pd.read_csv('human_proteome.csv')

In [9]:
seqs = []
for i, row in sources.iloc[0:10000, :].iterrows():
    seqs.append(SeqRecord(row['Source Sequence'], id=row['Source Accession'], description=''))

with open('sources.fasta', 'w') as f:
    SeqIO.write(seqs, f, 'fasta')

In [126]:
# read in BLAST results and take largest seq identity and largest alignment length per protein
columns = ['query', 'subject', '%_identity', 'alignment_length', 'mismatches', 'gap_opens', 'q_start', 'q_end', 's_start', 's_end', 'evalue', 'bit_score']
df = pd.read_csv('blast_output.csv', names=columns)

idx = df.groupby(['query'])['%_identity'].transform(max) == df['%_identity']
df = df[idx]

idx = df.groupby(['query'])['alignment_length'].transform(max) == df['alignment_length']
df = df[idx]

In [183]:
df

query                         subject  %_identity  \
0              P07333.2           sp|P07333|CSF1R_HUMAN       100.0   
686      XP_006710671.1           sp|Q5VUY2|ADCL4_HUMAN       100.0   
696         NP_997320.2  tr|A0A1C7CYW8|A0A1C7CYW8_HUMAN       100.0   
811      XP_005246254.1           sp|Q4ZG55|GREB1_HUMAN       100.0   
817          BAB13945.1          tr|H0YBE5|H0YBE5_HUMAN       100.0   
...                 ...                             ...         ...   
1677655     NP_005073.2           sp|Q14258|TRI25_HUMAN       100.0   
1677893     NP_115925.2           sp|Q96CW9|NTNG2_HUMAN       100.0   
1678013     NP_060716.2           sp|Q86WR0|CCD25_HUMAN       100.0   
1678019     NP_005500.4           sp|Q9Y485|DMXL1_HUMAN       100.0   
1678033     NP_775873.2           sp|Q9P265|DIP2B_HUMAN       100.0   

         alignment_length  mismatches  gap_opens  q_start  q_end  s_start  \
0                     972           0          0        1    972        1   
686                   340           0          0        1    340       68   
696                  4471           0          0        1   4471       62   
811                   947           0          0        1    947     1003   
817                   713           0          0        3    715        2   
...                   ...         ...        ...      ...    ...      ...   
1677655               630           0          0        1    630        1   
1677893               530           0          0        1    530        1   
1678013               208           0          0        1    208        1   
1678019              3027           0          0        1   3027        1   
1678033              1576           0          0        1   1576        1   

         s_end         evalue  bit_score subject_gene  
0          972   0.000000e+00     2026.0        CSF1R  
686        407   0.000000e+00      705.0      AADACL4  
696       4532   0.000000e+00     9265.0       DNAH10  
811       1949   0.000000e+00     1972.0        GREB1  
817        714   0.000000e+00     1481.0         ADGB  
...        ...            ...        ...          ...  
1677655    630   0.000000e+00     1310.0       TRIM25  
1677893    530   0.000000e+00     1102.0        NTNG2  
1678013    208  3.710000e-156      431.0       CCDC25  
1678019   3027   0.000000e+00     6292.0        DMXL1  
1678033   1576   0.000000e+00     3257.0        DIP2B  

[10036 rows x 13 columns]

## BLAST Results - No Matched Sequences

In [186]:
# number of source proteins
len(list(SeqIO.parse('sources.fasta', 'fasta')))
ids = [str(record.id) for record in list(SeqIO.parse('sources.fasta', 'fasta'))]
print('Number of test source antigens:')
print(len(ids))

Number of test source antigens:
10000


In [187]:
# number of source proteins with a BLAST match
print('Number of antigens that got a BLAST match:')
print(len(df['query'].unique()))

Number of antigens that got a BLAST match:
9968


In [130]:
set(ids) - set(df['query']) 

{'2BNQ_C',
 '3HG1_C',
 '660134A',
 'AAA18341.1',
 'AAD14388.1',
 'AAF74214.1',
 'AAG35548.1',
 'AAH30635.1',
 'AAL09582.1',
 'AAM03375.1',
 'AAO25648.1',
 'AAQ13601.1',
 'AAQ13645.1',
 'BAB21254.1',
 'BAJ83982.1',
 'BAJ83984.1',
 'CAA13575.1',
 'CAA13576.1',
 'EAW47713.1',
 'EAW52466.1',
 'EAW53866.1',
 'EAW64073.1',
 'EAW69107.1',
 'EAW79160.1',
 'Q6ZWC9',
 'Q969P4',
 'Q96ND5',
 'Q9BXV0.1',
 'Q9H627',
 'T14769',
 'XP_001133217.1',
 'XP_001722870.1'}

## BLAST Results - Matched Sequences

In [192]:
df[df['%_identity'] < 90]

query                  subject  %_identity  \
4229           P01815.1    sp|P01814|HV270_HUMAN      89.000   
4313           P01824.1    sp|P01824|HV439_HUMAN      80.808   
54051        EAL24379.1  sp|Q7Z6V5-2|ADAT2_HUMAN      81.481   
142110   XP_006723832.1     sp|O94906|PRP6_HUMAN      85.896   
167224       ABV03091.1    sp|P01780|HV307_HUMAN      89.691   
...                 ...                      ...         ...   
1266656      CAD89482.1    sp|P01824|HV439_HUMAN      85.859   
1266835      ACZ04887.1    sp|P01817|HV205_HUMAN      89.189   
1266920      BAI51348.1    sp|P01817|HV205_HUMAN      89.610   
1325547      CAC94328.1    sp|P01767|HV353_HUMAN      81.250   
1605523  NP_001193972.1   sp|P04439-2|HLAA_HUMAN      75.000   

         alignment_length  mismatches  gap_opens  q_start  q_end  s_start  \
4229                  100           8          1        1     97       20   
4313                   99          19          0        1     99       27   
54051                  27           5          0        1     27       27   
142110                943          56          7        1    868        1   
167224                 97          10          0        1     97       20   
...                   ...         ...        ...      ...    ...      ...   
1266656                99          14          0        1     99       27   
1266835                74           8          0        1     74       45   
1266920                77           8          0        1     77       42   
1325547                64          12          0        1     64       51   
1605523               112          28          0       78    189        3   

         s_end        evalue  bit_score subject_gene  
4229       119  1.720000e-60      182.0     IGHV2-70  
4313       125  8.350000e-52      161.0     IGHV4-39  
54051       53  4.100000e-08       52.0        ADAT2  
142110     941  0.000000e+00     1562.0        PRPF6  
167224     116  9.340000e-61      182.0      IGHV3-7  
...        ...           ...        ...          ...  
1266656    125  1.920000e-52      162.0     IGHV4-39  
1266835    118  4.570000e-47      147.0      IGHV2-5  
1266920    118  3.190000e-47      147.0      IGHV2-5  
1325547    114  1.700000e-34      114.0     IGHV3-53  
1605523    114  1.040000e-45      155.0        HLA-A  

[68 rows x 13 columns]

In [193]:
df[df['query'] == 'NP_997320.2']

query                         subject  %_identity  \
696  NP_997320.2  tr|A0A1C7CYW8|A0A1C7CYW8_HUMAN       100.0   

     alignment_length  mismatches  gap_opens  q_start  q_end  s_start  s_end  \
696              4471           0          0        1   4471       62   4532   

     evalue  bit_score subject_gene  
696     0.0     9265.0       DNAH10

In [133]:
epitope_map['NP_997320.2']

['NANVLHFLKNIICQ',
 'QDLSDVLQI',
 'NLSEETNIV',
 'LLLDLKNEALR',
 'WESQLRFYWDRE',
 'LTDRIYLTL']

In [134]:
# search in PEPMatch and get counts of protein IDs
matches = Matcher(epitope_map['NP_997320.2'], '9606_reference_with_isoforms', 0, 5, output_format='dataframe').match()
Counter(matches['Protein ID'])

Searching peptide #1
Searching peptide #2
Searching peptide #3
Searching peptide #4
Searching peptide #5
Searching peptide #6


Counter({'Q8IVF4.4': 6,
         'A0A1C7CYW8.1': 6,
         'A0A669KB38.1': 6,
         'Q8IVF4-2': 2,
         'A0A087WV07.1': 1,
         'A0A0J9YY17.1': 4,
         'F5H515.2': 2})

In [135]:
matches

Peptide Sequence Matched Sequence  Proteome       Species    Gene  \
0    NANVLHFLKNIICQ   NANVLHFLKNIICQ      9606  Homo sapiens  DNAH10   
1    NANVLHFLKNIICQ   NANVLHFLKNIICQ      9606  Homo sapiens  DNAH10   
2    NANVLHFLKNIICQ   NANVLHFLKNIICQ      9606  Homo sapiens  DNAH10   
3    NANVLHFLKNIICQ   NANVLHFLKNIICQ      9606  Homo sapiens    None   
4         QDLSDVLQI        QDLSDVLQI      9606  Homo sapiens  DNAH10   
5         QDLSDVLQI        QDLSDVLQI      9606  Homo sapiens  DNAH10   
6         QDLSDVLQI        QDLSDVLQI      9606  Homo sapiens  DNAH10   
7         QDLSDVLQI        QDLSDVLQI      9606  Homo sapiens  DNAH10   
8         QDLSDVLQI        QDLSDVLQI      9606  Homo sapiens    None   
9         NLSEETNIV        NLSEETNIV      9606  Homo sapiens  DNAH10   
10        NLSEETNIV        NLSEETNIV      9606  Homo sapiens  DNAH10   
11        NLSEETNIV        NLSEETNIV      9606  Homo sapiens  DNAH10   
12        NLSEETNIV        NLSEETNIV      9606  Homo sapiens  DNAH10   
13      LLLDLKNEALR      LLLDLKNEALR      9606  Homo sapiens  DNAH10   
14      LLLDLKNEALR      LLLDLKNEALR      9606  Homo sapiens  DNAH10   
15      LLLDLKNEALR      LLLDLKNEALR      9606  Homo sapiens  DNAH10   
16      LLLDLKNEALR      LLLDLKNEALR      9606  Homo sapiens  DNAH10   
17     WESQLRFYWDRE     WESQLRFYWDRE      9606  Homo sapiens  DNAH10   
18     WESQLRFYWDRE     WESQLRFYWDRE      9606  Homo sapiens  DNAH10   
19     WESQLRFYWDRE     WESQLRFYWDRE      9606  Homo sapiens  DNAH10   
20     WESQLRFYWDRE     WESQLRFYWDRE      9606  Homo sapiens  DNAH10   
21     WESQLRFYWDRE     WESQLRFYWDRE      9606  Homo sapiens  DNAH10   
22        LTDRIYLTL        LTDRIYLTL      9606  Homo sapiens  DNAH10   
23        LTDRIYLTL        LTDRIYLTL      9606  Homo sapiens  DNAH10   
24        LTDRIYLTL        LTDRIYLTL      9606  Homo sapiens  DNAH10   
25        LTDRIYLTL        LTDRIYLTL      9606  Homo sapiens  DNAH10   
26        LTDRIYLTL        LTDRIYLTL      9606  Homo sapiens  DNAH10   

      Protein ID                                 Protein Name  Mismatches  \
0       Q8IVF4.4               Dynein axonemal heavy chain 10           0   
1   A0A1C7CYW8.1               Dynein axonemal heavy chain 10           0   
2   A0A669KB38.1               Dynein axonemal heavy chain 10           0   
3       Q8IVF4-2  Isoform 2 of Dynein axonemal heavy chain 10           0   
4       Q8IVF4.4               Dynein axonemal heavy chain 10           0   
5   A0A1C7CYW8.1               Dynein axonemal heavy chain 10           0   
6   A0A669KB38.1               Dynein axonemal heavy chain 10           0   
7   A0A087WV07.1               Dynein axonemal heavy chain 10           0   
8       Q8IVF4-2  Isoform 2 of Dynein axonemal heavy chain 10           0   
9       Q8IVF4.4               Dynein axonemal heavy chain 10           0   
10  A0A0J9YY17.1    Dynein axonemal heavy chain 10 (Fragment)           0   
11  A0A1C7CYW8.1               Dynein axonemal heavy chain 10           0   
12  A0A669KB38.1               Dynein axonemal heavy chain 10           0   
13      Q8IVF4.4               Dynein axonemal heavy chain 10           0   
14  A0A0J9YY17.1    Dynein axonemal heavy chain 10 (Fragment)           0   
15  A0A1C7CYW8.1               Dynein axonemal heavy chain 10           0   
16  A0A669KB38.1               Dynein axonemal heavy chain 10           0   
17      Q8IVF4.4               Dynein axonemal heavy chain 10           0   
18  A0A0J9YY17.1    Dynein axonemal heavy chain 10 (Fragment)           0   
19  A0A1C7CYW8.1               Dynein axonemal heavy chain 10           0   
20  A0A669KB38.1               Dynein axonemal heavy chain 10           0   
21      F5H515.2    Dynein axonemal heavy chain 10 (Fragment)           0   
22      Q8IVF4.4               Dynein axonemal heavy chain 10           0   
23  A0A0J9YY17.1    Dynein axonemal heavy chain 10 (Fragment)           0   
24  A0A1C7CYW8.1               Dynein axonemal heavy chain 10

## Remove Duplicates with Same Subject Gene

In [137]:
# assign genes to IDs using proteome mappings
gene_id_map = dict(zip(hp['id'], hp['gene']))

df['subject_gene'] = df['subject'].str.split('|').str[1].map(gene_id_map)

df.drop_duplicates(subset=['query', 'subject_gene'],col inplace=True)

## Compare Just BLAST and Just PEPMatch results

In [138]:
blast_results = {}
for i, row in df.iterrows():
    blast_results[row['query']] = row['subject_gene']

In [139]:
pepmatch_results = {}
for record in list(SeqIO.parse('sources.fasta', 'fasta')):
    try:
        matches = Matcher(epitope_map[record.id], '9606_reference_with_isoforms', 0, 5, best_match=True, output_format='dataframe').match()
        pepmatch_results[record.id] = Counter(matches['Gene']).most_common()[0][0]
    except KeyError:
        continue

Searching peptide #1
Searching peptide #2
Searching peptide #3
Searching peptide #4
Searching peptide #5
Searching peptide #6
Searching peptide #7
Searching peptide #8
Searching peptide #9
Searching peptide #10
Searching peptide #1
Searching peptide #1
Searching peptide #2
Searching peptide #3
Searching peptide #4
Searching peptide #5
Searching peptide #6
Searching peptide #1
Searching peptide #1
Searching peptide #1
Searching peptide #1
Searching peptide #1
Searching peptide #1
Searching peptide #2
Searching peptide #1
Searching peptide #1
Searching peptide #1
Searching peptide #2
Searching peptide #3
Searching peptide #4
Searching peptide #5
Searching peptide #6
Searching peptide #7
Searching peptide #8
Searching peptide #9
Searching peptide #10
Searching peptide #11
Searching peptide #12
Searching peptide #13
Searching peptide #14
Searching peptide #15
Searching peptide #16
Searching peptide #17
Searching peptide #18
Searching peptide #19
Searching peptide #20
Searching peptide #21


Searching peptide #14
Searching peptide #15
Searching peptide #16
Searching peptide #17
Searching peptide #18
Searching peptide #19
Searching peptide #20
Searching peptide #21
Searching peptide #22
Searching peptide #23
Searching peptide #24
Searching peptide #25
Searching peptide #26
Searching peptide #1
Searching peptide #2
Searching peptide #3
Searching peptide #4
Searching peptide #5
Searching peptide #6
Searching peptide #7
Searching peptide #8
Searching peptide #9
Searching peptide #10
Searching peptide #11
Searching peptide #12
Searching peptide #13
Searching peptide #14
Searching peptide #15
Searching peptide #16
Searching peptide #17
Searching peptide #18
Searching peptide #19
Searching peptide #20
Searching peptide #21
Searching peptide #22
Searching peptide #23
Searching peptide #24
Searching peptide #25
Searching peptide #26
Searching peptide #27
Searching peptide #28
Searching peptide #29
Searching peptide #30
Searching peptide #31
Searching peptide #1
Searching peptide #2

Searching peptide #31
Searching peptide #32
Searching peptide #33
Searching peptide #34
Searching peptide #35
Searching peptide #36
Searching peptide #37
Searching peptide #38
Searching peptide #1
Searching peptide #2
Searching peptide #3
Searching peptide #4
Searching peptide #5
Searching peptide #6
Searching peptide #7
Searching peptide #8
Searching peptide #9
Searching peptide #10
Searching peptide #11
Searching peptide #12
Searching peptide #13
Searching peptide #14
Searching peptide #15
Searching peptide #16
Searching peptide #17
Searching peptide #18
Searching peptide #19
Searching peptide #20
Searching peptide #21
Searching peptide #22
Searching peptide #23
Searching peptide #24
Searching peptide #25
Searching peptide #26
Searching peptide #27
Searching peptide #28
Searching peptide #29
Searching peptide #30
Searching peptide #31
Searching peptide #32
Searching peptide #33
Searching peptide #34
Searching peptide #35
Searching peptide #36
Searching peptide #37
Searching peptide #

Searching peptide #1
Searching peptide #2
Searching peptide #3
Searching peptide #4
Searching peptide #5
Searching peptide #6
Searching peptide #7
Searching peptide #8
Searching peptide #9
Searching peptide #10
Searching peptide #11
Searching peptide #12
Searching peptide #13
Searching peptide #14
Searching peptide #15
Searching peptide #16
Searching peptide #17
Searching peptide #18
Searching peptide #1
Searching peptide #1
Searching peptide #2
Searching peptide #3
Searching peptide #4
Searching peptide #1
Searching peptide #2
Searching peptide #3
Searching peptide #4
Searching peptide #5
Searching peptide #1
Searching peptide #1
Searching peptide #2
Searching peptide #3
Searching peptide #4
Searching peptide #5
Searching peptide #6
Searching peptide #7
Searching peptide #8
Searching peptide #9
Searching peptide #10
Searching peptide #11
Searching peptide #12
Searching peptide #13
Searching peptide #14
Searching peptide #15
Searching peptide #1
Searching peptide #1
Searching peptide #

Searching peptide #1
Searching peptide #1
Searching peptide #2
Searching peptide #3
Searching peptide #1
Searching peptide #2
Searching peptide #3
Searching peptide #4
Searching peptide #5
Searching peptide #6
Searching peptide #7
Searching peptide #8
Searching peptide #9
Searching peptide #10
Searching peptide #11
Searching peptide #12
Searching peptide #13
Searching peptide #14
Searching peptide #1
Searching peptide #2
Searching peptide #3
Searching peptide #4
Searching peptide #5
Searching peptide #6
Searching peptide #7
Searching peptide #8
Searching peptide #9
Searching peptide #10
Searching peptide #11
Searching peptide #12
Searching peptide #13
Searching peptide #14
Searching peptide #15
Searching peptide #16
Searching peptide #17
Searching peptide #18
Searching peptide #19
Searching peptide #1
Searching peptide #2
Searching peptide #1
Searching peptide #2
Searching peptide #3
Searching peptide #4
Searching peptide #5
Searching peptide #6
Searching peptide #7
Searching peptide #

...

Searching peptide #1
Searching peptide #2
Searching peptide #3
Searching peptide #4
Searching peptide #5
Searching peptide #6
Searching peptide #7
Searching peptide #8
Searching peptide #9
Searching peptide #10
Searching peptide #11
Searching peptide #12
Searching peptide #1
Searching peptide #2
Searching peptide #3
Searching peptide #4
Searching peptide #1
Searching peptide #2
Searching peptide #3
Searching peptide #4
Searching peptide #5
Searching peptide #1
Searching peptide #1
Searching peptide #2
Searching peptide #1
Searching peptide #2
Searching peptide #1
Searching peptide #2
Searching peptide #3
Searching peptide #4
Searching peptide #1
Searching peptide #2
Searching peptide #3
Searching peptide #4
Searching peptide #5
Searching peptide #6
Searching peptide #7
Searching peptide #8
Searching peptide #9
Searching peptide #10
Searching peptide #11
Searching peptide #12
Searching peptide #13
Searching peptide #14
Searching peptide #1
Searching peptide #2
Searching peptide #3
Searc

Searching peptide #1
Searching peptide #1
Searching peptide #2
Searching peptide #3
Searching peptide #4
Searching peptide #1
Searching peptide #1
Searching peptide #2
Searching peptide #1
Searching peptide #2
Searching peptide #3
Searching peptide #4
Searching peptide #5
Searching peptide #6
Searching peptide #7
Searching peptide #8
Searching peptide #9
Searching peptide #10
Searching peptide #11
Searching peptide #12
Searching peptide #13
Searching peptide #14
Searching peptide #15
Searching peptide #16
Searching peptide #17
Searching peptide #18
Searching peptide #19
Searching peptide #20
Searching peptide #21
Searching peptide #22
Searching peptide #23
Searching peptide #24
Searching peptide #25
Searching peptide #26
Searching peptide #27
Searching peptide #28
Searching peptide #29
Searching peptide #30
Searching peptide #31
Searching peptide #32
Searching peptide #33
Searching peptide #34
Searching peptide #35
Searching peptide #36
Searching peptide #37
Searching peptide #38
Searc

Searching peptide #1
Searching peptide #2
Searching peptide #3
Searching peptide #4
Searching peptide #5
Searching peptide #6
Searching peptide #7
Searching peptide #8
Searching peptide #9
Searching peptide #10
Searching peptide #11
Searching peptide #12
Searching peptide #13
Searching peptide #14
Searching peptide #15
Searching peptide #16
Searching peptide #17
Searching peptide #18
Searching peptide #19
Searching peptide #20
Searching peptide #21
Searching peptide #22
Searching peptide #23
Searching peptide #24
Searching peptide #25
Searching peptide #26
Searching peptide #27
Searching peptide #28
Searching peptide #29
Searching peptide #30
Searching peptide #31
Searching peptide #32
Searching peptide #33
Searching peptide #34
Searching peptide #35
Searching peptide #36
Searching peptide #37
Searching peptide #38
Searching peptide #39
Searching peptide #40
Searching peptide #41
Searching peptide #1
Searching peptide #2
Searching peptide #3
Searching peptide #4
Searching peptide #5
Se

Searching peptide #1
Searching peptide #2
Searching peptide #1
Searching peptide #2
Searching peptide #1
Searching peptide #2
Searching peptide #3
Searching peptide #4
Searching peptide #5
Searching peptide #6
Searching peptide #7
Searching peptide #8
Searching peptide #9
Searching peptide #10
Searching peptide #11
Searching peptide #12
Searching peptide #13
Searching peptide #14
Searching peptide #15
Searching peptide #16
Searching peptide #17
Searching peptide #18
Searching peptide #19
Searching peptide #20
Searching peptide #21
Searching peptide #22
Searching peptide #1
Searching peptide #1
Searching peptide #2
Searching peptide #1
Searching peptide #2
Searching peptide #3
Searching peptide #1
Searching peptide #2
Searching peptide #3
Searching peptide #4
Searching peptide #5
Searching peptide #6
Searching peptide #1
Searching peptide #2
Searching peptide #3
Searching peptide #4
Searching peptide #5
Searching peptide #6
Searching peptide #7
Searching peptide #8
Searching peptide #9


ValueError: A peptide in the query contains a lowercase letter.

In [140]:
sources = [record.id for record in list(SeqIO.parse('sources.fasta', 'fasta'))]

In [141]:
results = pd.DataFrame(sources, columns=['source'])
results['BLAST'] = results['source'].map(blast_results)
results['PEPMatch'] = results['source'].map(pepmatch_results)

In [142]:
results[results['BLAST'] != results['PEPMatch']]

source    BLAST PEPMatch
8      CAA08965.1    HLA-B         
9          3QDM_D   TRAV35         
12         4P4K_C   TRAJ28  TRAV9-2
17     AAH70302.1    AMY1C    AMY1B
22     BAF82896.1  TIMM17B      NaN
...           ...      ...      ...
9995  NP_005073.2   TRIM25      NaN
9996  NP_115925.2    NTNG2      NaN
9997  NP_060716.2   CCDC25      NaN
9998  NP_005500.4    DMXL1      NaN
9999  NP_775873.2    DIP2B      NaN

[6996 rows x 3 columns]

In [143]:
(results['PEPMatch'].isna()).value_counts()

True     6653
False    3347
Name: PEPMatch, dtype: int64

In [144]:
matches = Matcher(epitope_map['3QDM_D'], '9606_reference_with_isoforms', 0, 5, best_match=True, output_format='dataframe').match()
pepmatch_results[record.id] = Counter(matches['Gene']).most_common()[0][0]

Searching peptide #1


In [145]:
matches

Peptide Sequence Matched Sequence Proteome Species Gene Protein ID  \
0  DPGEGPVLLIALYKAGELTSN                                                     

  Protein Name Mismatches Index start Index end Protein Existence Level  \
0                                                                         

  Gene Priority  
0

## BLAST Duplicates with Different Genes

In [146]:
duplicates = list(df[df['query'].duplicated()]['query'].unique())
len(duplicates)

59

In [147]:
df[df['query'].duplicated()]

query                         subject  %_identity  \
21328          P35226.2            sp|P35226|BMI1_HUMAN     100.000   
23526        CAR92541.1          tr|E7ENX8|E7ENX8_HUMAN     100.000   
28933          O95766.1            sp|P86791|CCZ1_HUMAN     100.000   
63515          Q8IYE1.2  tr|A0A3B3IRZ5|A0A3B3IRZ5_HUMAN     100.000   
115817   XP_005273882.1  tr|A0A1B0GVQ7|A0A1B0GVQ7_HUMAN      98.678   
...                 ...                             ...         ...   
1602166        A0A5B9.1           sp|P0DTU4|TRBR2_HUMAN     100.000   
1608046     NP_001734.1           sp|P0DP24|CALM2_HUMAN     100.000   
1608047     NP_001734.1           sp|P0DP23|CALM1_HUMAN     100.000   
1610228  NP_001157941.1  tr|A0A0A6YYA0|A0A0A6YYA0_HUMAN     100.000   
1610229  NP_001157941.1         sp|Q86XR7-2|TCAM2_HUMAN     100.000   

         alignment_length  mismatches  gap_opens  q_start  q_end  s_start  \
21328                 326           0          0        1    326        1   
23526                 209           0          0        1    209        1   
28933                 482           0          0        1    482        1   
63515                 715           0          0        1    715       24   
115817                227           3          0      453    679      145   
...                   ...         ...        ...      ...    ...      ...   
1602166               178           0          0        1    178      138   
1608046               149           0          0        1    149        1   
1608047               149           0          0        1    149        1   
1610228               188           0          0        1    188        1   
1610229               188           0          0        1    188        1   

         s_end         evalue  bit_score  subject_gene  
21328      326   0.000000e+00      682.0          BMI1  
23526      209  9.050000e-140      412.0           NaN  
28933      482   0.000000e+00     1007.0          CCZ1  
63515      738   0.000000e+00     1429.0           NaN  
115817     371  1.330000e-158      462.0           NaN  
...        ...            ...        ...           ...  
1602166    315  8.980000e-133      375.0           TRB  
1608046    149  1.230000e-105      298.0         CALM2  
1608047    149  1.230000e-105      298.0         CALM1  
1610228    188  3.160000e-143      397.0  TMED7-TICAM2  
1610229    188  4.370000e-141      400.0        TICAM2  

[68 rows x 13 columns]

In [122]:
df[df['query'].duplicated()][df[df['query'].duplicated()]['subject_gene'].str.contains('-') == False]

query                         subject  %_identity  \
21328          P35226.2            sp|P35226|BMI1_HUMAN     100.000   
28933          O95766.1            sp|P86791|CCZ1_HUMAN     100.000   
130342           P02248            sp|P62987|RL40_HUMAN     100.000   
130343           P02248          tr|J3QS39|J3QS39_HUMAN     100.000   
130345           P02248          tr|F5H6Q2|F5H6Q2_HUMAN     100.000   
359709           Q15285  tr|A0A804HKM6|A0A804HKM6_HUMAN      96.970   
359715           Q15285            sp|P01111|RASN_HUMAN      96.970   
374192       AAA52697.1           sp|P0DMV8|HS71A_HUMAN      99.532   
395281         P08107.5           sp|P0DMV8|HS71A_HUMAN     100.000   
427471         O14896.1            sp|O14896|IRF6_HUMAN     100.000   
470779           1XDA_B          tr|C9JNR5|C9JNR5_HUMAN     100.000   
529054         P62158.2           sp|P0DP24|CALM2_HUMAN     100.000   
529055         P62158.2           sp|P0DP23|CALM1_HUMAN     100.000   
567956           A0AUL6  tr|A0A6Q8PFE4|A0A6Q8PFE4_HUMAN     100.000   
599049       EAX03082.1           sp|P06899|H2B1J_HUMAN     100.000   
710703       CAA41050.1           sp|Q6FI13|H2A2A_HUMAN     100.000   
729048       EAX04505.1          tr|J3QS39|J3QS39_HUMAN     100.000   
773711       AAD14420.1             sp|P68871|HBB_HUMAN     100.000   
777793       CAA39189.1            sp|P69892|HBG2_HUMAN     100.000   
802455       AAA59844.1           sp|P0DMV8|HS71A_HUMAN     100.000   
968689   NP_001159578.1           sp|P0DP25|CALM3_HUMAN     100.000   
968691   NP_001159578.1           sp|P0DP24|CALM2_HUMAN     100.000   
980249      NP_057053.1          tr|I3L0E3|I3L0E3_HUMAN     100.000   
1032367     NP_542163.1            sp|P0C0S8|H2A1_HUMAN     100.000   
1072452     NP_055378.1           sp|P0DI82|TPC2B_HUMAN     100.000   
1177881        P86790.1            sp|P86791|CCZ1_HUMAN     100.000   
1241514        Q96KK5.3            sp|P0C0S8|H2A1_HUMAN     100.000   
1309762      AAH10130.1            sp|P86791|CCZ1_HUMAN     100.000   
1315746  NP_001139653.1           sp|B7ZW38|HNRC3_HUMAN     100.000   
1317462      CAD97797.1           sp|Q99598|TSNAX_HUMAN     100.000   
1547857        Q8WWN9.1           sp|G9CGD6|CNIPF_HUMAN     100.000   
1567164     NP_932765.1            sp|P86791|CCZ1_HUMAN     100.000   
1602166        A0A5B9.1           sp|P0DTU4|TRBR2_HUMAN     100.000   
1608046     NP_001734.1           sp|P0DP24|CALM2_HUMAN     100.000   
1608047     NP_001734.1           sp|P0DP23|CALM1_HUMAN     100.000   
1610229  NP_001157941.1         sp|Q86XR7-2|TCAM2_HUMAN     100.000   

         alignment_length  mismatches  gap_opens  q_start  q_end  s_start  \
21328                 326           0          0        1    326        1   
28933                 482           0          0        1    482        1   
130342                 76           0          0        1     76        1   
130343                 76           0          0        1     76        1   
130345                 76           0          0        1     76        1   
359709                 33           1          0        1     33        1   
359715                 33           1          0        1     33        1   
374192                641           2          1        1    640        1   
395281                641           0          0        1    641        1   
427471                467           0          0        1    467        1   
470779                 29           0          0        1     29       25   
529054                149           0          0        1    149        1   
529055                149           0          0        1    149        1   
567956                 95           0          0        4     98       68   
599049                 76           0          0        1     76        1   
710703                 57           0          0        1     57        1   
729048                 93           0          0        1     93        1   
7737

In [163]:
set(epitope_map['P02248'])

{'GRTLSDYNI', 'IFVKTLTGKTITLEVEPS', 'KESTLHLVL'}

In [164]:
matches = Matcher(epitope_map['P02248'], '9606_reference_with_isoforms', 0, 5, best_match=True, output_format='dataframe').match()

Searching peptide #1
Searching peptide #2
Searching peptide #3
Searching peptide #4
Searching peptide #5


In [165]:
matches

Peptide Sequence    Matched Sequence  Proteome       Species Gene  \
0            KESTLHLVL           KESTLHLVL      9606  Homo sapiens  UBB   
37           GRTLSDYNI           GRTLSDYNI      9606  Homo sapiens  UBB   
76  IFVKTLTGKTITLEVEPS  IFVKTLTGKTITLEVEPS      9606  Homo sapiens  UBB   

   Protein ID     Protein Name  Mismatches  Index start  Index end  \
0    P0CG47.1  Polyubiquitin-B           0           63         71   
37   P0CG47.1  Polyubiquitin-B           0           53         61   
76   P0CG47.1  Polyubiquitin-B           0            3         20   

    Protein Existence Level  Gene Priority  
0                         1              0  
37                        1              0  
76                        1              0

In [166]:
print(Counter(matches['Gene']))
Counter(matches['Gene']).most_common()[0][0]

Counter({'UBB': 3})


'UBB'

In [176]:
df[df['query'] == 'NP_542163.1']

query                subject  %_identity  alignment_length  \
1032366  NP_542163.1  sp|Q96KK5|H2A1H_HUMAN       100.0               128   
1032367  NP_542163.1   sp|P0C0S8|H2A1_HUMAN       100.0               128   

         mismatches  gap_opens  q_start  q_end  s_start  s_end        evalue  \
1032366           0          0        1    128        1    128  1.650000e-88   
1032367           0          0        1    128        1    128  1.860000e-88   

         bit_score subject_gene  
1032366      253.0       H2AC12  
1032367      253.0       H2AC17

In [177]:
set(epitope_map['NP_001734.1'])

{'ADIDGDGQVN',
 'ADIDGDGQVNY',
 'ADIDGDGQVNYE',
 'ADIDGDGQVNYEE',
 'ADIDGDGQVNYEEF',
 'ADQLTEEQIAEFK',
 'ADQLTEEQIAEFKEA',
 'AEFKEAFS',
 'AEFKEAFSL',
 'AEFKEAFSLF',
 'AELRHVMTNL',
 'DGNGYISAA',
 'DGQVNYEEFVQMMTAK',
 'DIDGDGQVN',
 'DIDGDGQVNY',
 'DIDGDGQVNYEE',
 'DIDGDGQVNYEEF',
 'DKDGNGYISA',
 'DTDSEEEIREAFR',
 'EAFSLFDKDGDGTITTK',
 'EEIREAFRV',
 'EEIREAFRVF',
 'FKEAFSLF',
 'FRVFDKDGN',
 'FVQMMTAK',
 'GDGQVNYEEF',
 'GDGQVNYEEFVQMMTAK',
 'GQNPTEAEL',
 'GQVNYEEF',
 'GQVNYEEFV',
 'GQVNYEEFVQMMTAK',
 'GTIDFPEFLTM',
 'GTVMRSLGQNPTE',
 'HVMTNLGE',
 'IAEFKEAFSLFDKDG',
 'IAEFKEAFSLFDKDGDG',
 'IDGDGQVNYEEFVQMMTAK',
 'IREADIDGD',
 'IREADIDGDG',
 'IREADIDGDGQVN',
 'IREADIDGDGQVNY',
 'IREADIDGDGQVNYEEF',
 'KELGTVMRSL',
 'KMKDTDSEEEI',
 'LRHVMTNL',
 'MIREADIDGDGQVN',
 'MIREADIDGDGQVNYEEFVQMMTAK',
 'NGYISAAELRHVMT',
 'PTEAELQD',
 'READIDGDGQV',
 'READIDGDGQVN',
 'READIDGDGQVNY',
 'RSLGQNPTEAEL',
 'RVFDKDGNGY',
 'SAAELRHVM',
 'SEEEIREAF',
 'TITTKELGTVMR',
 'TTKELGTVMR',
 'VDADGNGTIDF',
 'VFDKDGNGYISA

In [178]:
matches = Matcher(epitope_map['NP_001734.1'], '9606_reference_with_isoforms', 0, 5, best_match=True, output_format='dataframe').match()

Searching peptide #1
Searching peptide #2
Searching peptide #3
Searching peptide #4
Searching peptide #5
Searching peptide #6
Searching peptide #7
Searching peptide #8
Searching peptide #9
Searching peptide #10
Searching peptide #11
Searching peptide #12
Searching peptide #13
Searching peptide #14
Searching peptide #15
Searching peptide #16
Searching peptide #17
Searching peptide #18
Searching peptide #19
Searching peptide #20
Searching peptide #21
Searching peptide #22
Searching peptide #23
Searching peptide #24
Searching peptide #25
Searching peptide #26
Searching peptide #27
Searching peptide #28
Searching peptide #29
Searching peptide #30
Searching peptide #31
Searching peptide #32
Searching peptide #33
Searching peptide #34
Searching peptide #35
Searching peptide #36
Searching peptide #37
Searching peptide #38
Searching peptide #39
Searching peptide #40
Searching peptide #41
Searching peptide #42
Searching peptide #43
Searching peptide #44
Searching peptide #45
Searching peptide #

In [179]:
matches

Peptide Sequence Matched Sequence  Proteome       Species   Gene  \
0          SAAELRHVM        SAAELRHVM      9606  Homo sapiens  CALM1   
8         AELRHVMTNL       AELRHVMTNL      9606  Homo sapiens  CALM1   
15        EEIREAFRVF       EEIREAFRVF      9606  Homo sapiens  CALM1   
25         SEEEIREAF        SEEEIREAF      9606  Homo sapiens  CALM1   
34     IREADIDGDGQVN    IREADIDGDGQVN      9606  Homo sapiens  CALM1   
..               ...              ...       ...           ...    ...   
416   IREADIDGDGQVNY   IREADIDGDGQVNY      9606  Homo sapiens  CALM1   
423         GQVNYEEF         GQVNYEEF      9606  Homo sapiens  CALM1   
430       IREADIDGDG       IREADIDGDG      9606  Homo sapiens  CALM1   
437       DIDGDGQVNY       DIDGDGQVNY      9606  Homo sapiens  CALM1   
444       GDGQVNYEEF       GDGQVNYEEF      9606  Homo sapiens  CALM1   

    Protein ID  Protein Name  Mismatches  Index start  Index end  \
0     P0DP23.1  Calmodulin-1           0          102        110   
8     P0DP23.1  Calmodulin-1           0          104        113   
15    P0DP23.1  Calmodulin-1           0           84         93   
25    P0DP23.1  Calmodulin-1           0           82         90   
34    P0DP23.1  Calmodulin-1           0          126        138   
..         ...           ...         ...          ...        ...   
416   P0DP23.1  Calmodulin-1           0          126        139   
423   P0DP23.1  Calmodulin-1           0          135        142   
430   P0DP23.1  Calmodulin-1           0          126        135   
437   P0DP23.1  Calmodulin-1           0          130        139   
444   P0DP23.1  Calmodulin-1           0          133        142   

     Protein Existence Level  Gene Priority  
0                          1              0  
8                          1              0  
15                         1              0  
25                         1              0  
34                         1              0  
..                       ...            ...  
416                        1              0  
423                        1              0  
430                        1              0  
437                        1              0  
444                        1              0  

[61 rows x 12 columns]

In [181]:
print(Counter(matches['Gene']))
Counter(matches['Gene']).most_common()[0][0]

Counter({'CALM1': 61})


'CALM1'